In [1]:
!git clone https://github.com/DANGTHANHMY/HOSSemEval-EB23.git

Cloning into 'HOSSemEval-EB23'...
remote: Enumerating objects: 162, done.
remote: Counting objects: 100% (17/17), done.
remote: Compressing objects: 100% (14/14), done.
remote: Total 162 (delta 3), reused 13 (delta 3), pack-reused 145 (from 1)
Receiving objects: 100% (162/162), 22.00 MiB | 13.38 MiB/s, done.
Resolving deltas: 100% (70/70), done.
Updating files: 100% (77/77), done.


In [2]:
!ls

HOSSemEval-EB23  __notebook__.ipynb


In [3]:
!pip install -r "/kaggle/working/HOSSemEval-EB23/requirements.txt"

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.0/57.0 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.8/61.8 kB 3.6 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of sentence-transformers to determine which version is compatible with other requirements. This could take a while.
INFO: pip is still looking at multiple versions of sentence-transformers to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 5.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... - \ done
INFO: pip is looking at multiple versions of torch to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 33.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 829.5/829.5 kB 38.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.1/77.1 kB 5.1 MB/s eta 0:00:00
   ━━━━━━━━

In [4]:
%cd /kaggle/working/HOSSemEval-EB23/TAS/data

/kaggle/working/HOSSemEval-EB23/TAS/data


In [5]:
!python data_preprocessing_for_TAS.py --dataset absa_dataset_en

entity_sum:  3185
max_sen_len:  70
sample ratio:  3184 - 55712
entity_sum:  1295
max_sen_len:  71
sample ratio:  1294 - 22412


In [6]:
%cd /kaggle/working/HOSSemEval-EB23/TAS/TAS-Transformers/

/kaggle/working/HOSSemEval-EB23/TAS/TAS-Transformers


In [7]:
!pip install pytorch-crf

In [8]:
# vinai/phobert-base-v2
# avsolatorio/GIST-Embedding-v0
# intfloat/e5-large

In [9]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2023 NVIDIA Corporation
Built on Wed_Nov_22_10:17:15_PST_2023
Cuda compilation tools, release 12.3, V12.3.107
Build cuda_12.3.r12.3/compiler.33567101_0


In [10]:
!CUDA_VISIBLE_DEVICES=0 python TAS_BERT_joint.py \
--data_dir /kaggle/working/HOSSemEval-EB23/TAS/data/absa_dataset_en/three_joint/BIO/ \
--output_dir /kaggle/working/HOSSemEval-EB23/TAS/TAS-Transformers/results/absa_dataset_en/three_joint/BIO/my_result \
--model_name 'intfloat/e5-base' \
--vocab_file /kaggle/working/HOSSemEval-EB23/TAS/TAS-Transformers/Vocab/vocab.txt \
--tokenize_method word_split \
--use_crf \
--eval_test \
--do_lower_case \
--max_seq_length 128 \
--train_batch_size 32 \
--eval_batch_size 32 \
--learning_rate 2e-5 \
--num_train_epochs 20

['[PAD]', '[CLS]', 'B', 'I', 'O']
Downloading: 100%|█████████████████████████████| 645/645 [00:00<00:00, 3.44MB/s]
Downloading: 100%|███████████████████████████| 418M/418M [00:08<00:00, 54.2MB/s]
/opt/conda/lib/python3.10/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use thePyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
output_log_file= /kaggle/working/HOSSemEval-EB23/TAS/TAS-Transformers/results/absa_dataset_en/three_joint/BIO/my_result/log.txt
Iteration:   0%|                                       | 0/1841 [00:00<?, ?it/s]/opt/conda/lib/python3.10/site-packages/torchcrf/__init__.py:249: UserWarning: where received a uint8 condition tensor. This behavior is deprecated and will be removed in a future version of PyTorch. Use a boolean condition instead. (Triggered internally at ../aten/src/ATen/native/Tensor

In [11]:
!python evaluation_for_TSD_ASD_TASD.py \
--output_dir /kaggle/working/HOSSemEval-EB23/TAS/TAS-Transformers/results/absa_dataset_en/three_joint/BIO/my_result \
--num_epochs 20 \
--tag_schema BIO



The best result is in  test_ep_18  :
TASD task:
	All tuples
		P:  0.6496138996138996    R:  0.5200927357032458   F1:  0.5776824034334765
----------------------------------------------------

	Only NULL tuples
		P:  0.6581532416502947    R:  0.6085376930063578   F1:  0.632373761208117
----------------------------------------------------

	NO and pure O tag sequence
		P:  0.9780767534186149    R:  0.9893360699625201   F1:  0.9836741936914956
----------------------------------------------------


ASD task:
	P:  0.7693050193050193    R:  0.615919629057187   F1:  0.6841201716738198
----------------------------------------------------


TSD task containing NULL:
	P:  0.7596439169139466    R:  0.5939675174013921   F1:  0.6666666666666666
----------------------------------------------------


TSD task ignoring NULL:
	P:  0.2222222222222222    R:  0.02072538860103627   F1:  0.03791469194312796
----------------------------------------------------


